In [2]:
#IMPORT MODULES
import requests as http
from io import StringIO
from datetime import datetime
from datetime import timedelta

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
import plotly.express as px

from av_api import *
from av_load import *

In [3]:
# GET API KEY AND COMPANIES LIST
api_key = get_api_key()
ticks = get_tick_list('data/alpha_vantage/tick_list.txt')
ticks

['IBM', 'AAPL', 'NVDA']

In [4]:
price_data = load_price_data(ticks)
price_data['split_coefficient'].fillna(1)
price_data['cumm_split'] = price_data['split_coefficient'].groupby(level='tick').cumprod()
price_data

open     high     low   close  adjusted_close    volume  \
tick timestamp                                                               
IBM  2023-06-23  130.40  130.620  129.18  129.43      129.430000  11324705   
     2023-06-22  131.68  132.960  130.68  131.17      131.170000   6013021   
     2023-06-21  135.11  135.390  133.29  133.69      133.690000   5501272   
     2023-06-20  136.36  137.230  135.89  135.96      135.960000   4272511   
     2023-06-16  139.23  139.469  137.47  137.48      137.480000   7473676   
...                 ...      ...     ...     ...             ...       ...   
NVDA 1999-11-05   30.00   30.250   26.88   28.25        0.540064   1284100   
     1999-11-04   27.75   29.940   27.75   29.19        0.558034   2625700   
     1999-11-03   26.00   28.130   25.81   27.44        0.524579   4191000   
     1999-11-02   23.94   25.130   23.75   25.00        0.477933   1744800   
     1999-11-01   21.75   24.380   21.75   23.50        0.449257   1630300   

                 dividend_amount  split_coefficient  cumm_split  
tick timestamp                                                   
IBM  2023-06-23              0.0                1.0    1.000000  
     2023-06-22              0.0                1.0    1.000000  
     2023-06-21              0.0                1.0    1.000000  
     2023-06-20              0.0                1.0    1.000000  
     2023-06-16              0.0                1.0    1.000000  
...                          ...                ...         ...  
NVDA 1999-11-05              0.0                1.0   47.999976  
     1999-11-04              0.0                1.0   47.999976  
     1999-11-03              0.0                1.0   47.999976  
     1999-11-02              0.0                1.0   47.999976  
     1999-11-01              0.0                1.0   47.999976  

[17847 rows x 9 columns]

In [5]:
#BUILD FINAL DF
#final_df = []
#
#for tick in ticks:
#    tick_price_data  = price_data[price_data.index.get_level_values(0) == tick]
#    earnings_data = load_fundamentals('earnings_data', tick)
#    #cashflow_data = load_fundamentals('cashflow_data', tick)
#    #balance_sheets = load_fundamentals('balance_sheets', tick)
#    #income_statements = load_fundamentals('income_statements', tick)    
#    company_data = pd.concat([
#        tick_price_data,
#        earnings_data,
#        #cashflow_data, 
#        #balance_sheets, 
#        #income_statements 
#    ], axis='columns').sort_index(ascending=True).ffill()
#    final_df.append(company_data)
#final_df = pd.concat(final_df)

In [6]:
#final_df.loc['NVDA',:].dropna()

In [7]:
#time = final_df.loc['AAPL'].index
#eps = final_df.loc['AAPL', 'reportedEPS']
#pe_ratio = final_df.loc['AAPL', 'adjusted_close']
#pe_ratio = np.log(pe_ratio)
#pe_ratio_30 = pe_ratio - pe_ratio.shift(30)
#pe_ratio_90 = pe_ratio - pe_ratio.shift(90)
#fig, ax = plt.subplots(1, 1, figsize=(20, 10))
#plt.step(time, pe_ratio_30, label='30 day variation', alpha=.5)
#plt.step(time, pe_ratio_90, label='90 day variation', alpha=.5)
#plt.hlines(y=[0], xmin=datetime(1996, 1, 1), xmax=datetime(2024, 1, 1), colors=['r'])
#plt.legend()

In [8]:
def plot_series(data: pd.DataFrame, variable: str, alias: str, line_shape: str='', markers: str='', log_scale: bool=False):
    args = {
        'data_frame': data.reset_index(),
        'x': 'timestamp',
        'y': variable,
        'color':'tick',
        'title':alias,
        'labels':{
            'tick': 'Company',
            'timestamp': 'Date',
            variable: alias
        },
        'log_y':log_scale
    }
    if line_shape: 
        args['line_shape'] = line_shape
    if markers: 
        args['markers'] = markers
    px.line(**args).show()

In [9]:
plot_series(price_data, 'cumm_split', 'Cummulative Split', line_shape='hv')

In [10]:
# PLOT PRICE DATA
variable = 'adjusted_close'
alias = 'Adjusted Close'
plot_series(price_data, variable, alias, log_scale=True)

In [11]:
#BUILD EARNINGS DATA AND DROP ENTRIES WITH EXCESSIVE ADJUSTMENT
earnings_data = pd.concat([load_fundamentals('earnings_data', tick) for tick in ticks])
cummulative_split = earnings_data.join(price_data['cumm_split'], how='outer').sort_index(ascending=False).groupby(level='tick')['cumm_split'].ffill()
should_drop = earnings_data[earnings_data.join(cummulative_split)['cumm_split'] >= 30].index
earnings_data.drop(should_drop, inplace=True)
earnings_data

reportedDate  reportedEPS  estimatedEPS  surprise  \
tick timestamp                                                      
IBM  2023-03-31   2023-04-19         1.36          1.26      0.10   
     2022-12-31   2023-01-25         3.60          3.60      0.00   
     2022-09-30   2022-10-19         1.81          1.77      0.04   
     2022-06-30   2022-07-18         2.31          2.27      0.04   
     2022-03-31   2022-04-19         1.40          1.38      0.02   
...                      ...          ...           ...       ...   
NVDA 2001-07-31   2001-08-14         0.02          0.02      0.00   
     2001-04-30   2001-05-22         0.02          0.02      0.00   
     2001-01-31   2001-02-15         0.01          0.02     -0.01   
     2000-10-31   2000-11-09         0.01          0.01      0.00   
     2000-07-31   2000-08-21         0.01          0.01      0.00   

                 surprisePercentage  
tick timestamp                       
IBM  2023-03-31              7.9365  
     2022-12-31              0.0000  
     2022-09-30              2.2599  
     2022-06-30              1.7621  
     2022-03-31              1.4493  
...                             ...  
NVDA 2001-07-31              0.0000  
     2001-04-30              0.0000  
     2001-01-31            -50.0000  
     2000-10-31              0.0000  
     2000-07-31              0.0000  

[274 rows x 5 columns]

In [12]:
earnings_data.drop(columns=['reportedDate', 'surprise', 'surprisePercentage'], inplace=True, errors='ignore')
#earnings_data.dropna(inplace=True)
earnings_data

reportedEPS  estimatedEPS
tick timestamp                            
IBM  2023-03-31         1.36          1.26
     2022-12-31         3.60          3.60
     2022-09-30         1.81          1.77
     2022-06-30         2.31          2.27
     2022-03-31         1.40          1.38
...                      ...           ...
NVDA 2001-07-31         0.02          0.02
     2001-04-30         0.02          0.02
     2001-01-31         0.01          0.02
     2000-10-31         0.01          0.01
     2000-07-31         0.01          0.01

[274 rows x 2 columns]

In [13]:
# PLOT EARNINGS DATA

#period = 'quarterly'
variable = f'reportedEPS'
alias = variable
plot_series(earnings_data, variable, alias, line_shape='hv', markers='.')

In [14]:
price_data.drop(columns=['open', 'high', 'low', 'volume', 'dividend_amount', 'split_coefficient', 'cumm_split'], inplace=True, errors='ignore')
price_data

close  adjusted_close
tick timestamp                         
IBM  2023-06-23  129.43      129.430000
     2023-06-22  131.17      131.170000
     2023-06-21  133.69      133.690000
     2023-06-20  135.96      135.960000
     2023-06-16  137.48      137.480000
...                 ...             ...
NVDA 1999-11-05   28.25        0.540064
     1999-11-04   29.19        0.558034
     1999-11-03   27.44        0.524579
     1999-11-02   25.00        0.477933
     1999-11-01   23.50        0.449257

[17847 rows x 2 columns]

In [15]:
# DROP PRICE DATA FOR WHITCH WE DON'T HAVE EANRINGS DATA YET
for group, df in earnings_data.groupby(level='tick'):
    dates = price_data.index.get_level_values('timestamp')
    max_date = max(df.index.get_level_values('timestamp'))
    should_drop = price_data[dates > max_date].index
    price_data.drop(should_drop, inplace=True)

In [16]:

final_df = price_data.join(earnings_data, how='outer', sort=False).sort_index(ascending=False).groupby(level='tick').bfill()

for i in range(1, 8):
    reported_eps_gb = final_df.groupby(level=0)['reportedEPS']
    final_df[f'reportedEPS_{i}'] = reported_eps_gb.shift(-i)

final_df

close  adjusted_close  reportedEPS  estimatedEPS  \
tick timestamp                                                       
NVDA 2023-04-30  277.77      277.740355         1.09          0.92   
     2023-03-31  277.77      277.740355         0.88          0.81   
     2023-03-30  273.83      273.800775         0.88          0.81   
     2023-03-29  269.84      269.811201         0.88          0.81   
     2023-03-28  264.10      264.071814         0.88          0.81   
...                 ...             ...          ...           ...   
AAPL 1999-11-05   88.31        0.670080          NaN           NaN   
     1999-11-04   83.62        0.634493          NaN           NaN   
     1999-11-03   81.50        0.618407          NaN           NaN   
     1999-11-02   80.25        0.608922          NaN           NaN   
     1999-11-01   77.62        0.588966          NaN           NaN   

                 reportedEPS_1  reportedEPS_2  reportedEPS_3  reportedEPS_4  \
tick timestamp                                                                
NVDA 2023-04-30           0.88           0.88           0.88           0.88   
     2023-03-31           0.88           0.88           0.88           0.88   
     2023-03-30           0.88           0.88           0.88           0.88   
     2023-03-29           0.88           0.88           0.88           0.88   
     2023-03-28           0.88           0.88           0.88           0.88   
...                        ...            ...            ...            ...   
AAPL 1999-11-05            NaN            NaN            NaN            NaN   
     1999-11-04            NaN            NaN            NaN            NaN   
     1999-11-03            NaN            NaN            NaN            NaN   
     1999-11-02            NaN            NaN            NaN            NaN   
     1999-11-01            NaN            NaN            NaN            NaN   

                 reportedEPS_5  reportedEPS_6  reportedEPS_7  
tick timestamp                                                
NVDA 2023-04-30           0.88           0.88           0.88  
     2023-03-31           0.88           0.88           0.88  
     2023-03-30           0.88           0.88           0.88  
     2023-03-29           0.88           0.88           0.88  
     2023-03-28           0.88           0.88           0.88  
...                        ...            ...            ...  
AAPL 1999-11-05            NaN            NaN            NaN  
     1999-11-04            NaN            NaN            NaN  
     1999-11-03            NaN            NaN            NaN  
     1999-11-02            NaN            NaN            NaN  
     1999-11-01            NaN            NaN            NaN  

[17766 rows x 11 columns]

In [17]:
plot_series(final_df, 'reportedEPS', 'Reported EPS', line_shape='vh', markers='')

In [18]:

price_col = 'adjusted_close'
for column in final_df.columns:
    if column in price_data.columns: continue
    #final_df[column] = final_df[column] / final_df[price_col].groupby(level='tick').shift(-1)
    #final_df[column] = final_df[price_col] / final_df[column]
final_df

close  adjusted_close  reportedEPS  estimatedEPS  \
tick timestamp                                                       
NVDA 2023-04-30  277.77      277.740355         1.09          0.92   
     2023-03-31  277.77      277.740355         0.88          0.81   
     2023-03-30  273.83      273.800775         0.88          0.81   
     2023-03-29  269.84      269.811201         0.88          0.81   
     2023-03-28  264.10      264.071814         0.88          0.81   
...                 ...             ...          ...           ...   
AAPL 1999-11-05   88.31        0.670080          NaN           NaN   
     1999-11-04   83.62        0.634493          NaN           NaN   
     1999-11-03   81.50        0.618407          NaN           NaN   
     1999-11-02   80.25        0.608922          NaN           NaN   
     1999-11-01   77.62        0.588966          NaN           NaN   

                 reportedEPS_1  reportedEPS_2  reportedEPS_3  reportedEPS_4  \
tick timestamp                                                                
NVDA 2023-04-30           0.88           0.88           0.88           0.88   
     2023-03-31           0.88           0.88           0.88           0.88   
     2023-03-30           0.88           0.88           0.88           0.88   
     2023-03-29           0.88           0.88           0.88           0.88   
     2023-03-28           0.88           0.88           0.88           0.88   
...                        ...            ...            ...            ...   
AAPL 1999-11-05            NaN            NaN            NaN            NaN   
     1999-11-04            NaN            NaN            NaN            NaN   
     1999-11-03            NaN            NaN            NaN            NaN   
     1999-11-02            NaN            NaN            NaN            NaN   
     1999-11-01            NaN            NaN            NaN            NaN   

                 reportedEPS_5  reportedEPS_6  reportedEPS_7  
tick timestamp                                                
NVDA 2023-04-30           0.88           0.88           0.88  
     2023-03-31           0.88           0.88           0.88  
     2023-03-30           0.88           0.88           0.88  
     2023-03-29           0.88           0.88           0.88  
     2023-03-28           0.88           0.88           0.88  
...                        ...            ...            ...  
AAPL 1999-11-05            NaN            NaN            NaN  
     1999-11-04            NaN            NaN            NaN  
     1999-11-03            NaN            NaN            NaN  
     1999-11-02            NaN            NaN            NaN  
     1999-11-01            NaN            NaN            NaN  

[17766 rows x 11 columns]

In [19]:
# PLOT PRICE TO EARNINGS DATA
plot_series(final_df, 'estimatedEPS', 'Estimated EPS - Normalized')

In [20]:
final_df['daily_return'] = final_df['adjusted_close'] / final_df.groupby(level='tick')['adjusted_close'].shift(-1)
final_df['weekly_return'] = final_df['adjusted_close'] / final_df.groupby(level='tick')['adjusted_close'].shift(-5)
final_df['quarterly_return'] = final_df['adjusted_close'] / final_df.groupby(level='tick')['adjusted_close'].shift(-63)

In [21]:
plot_series(final_df, 'quarterly_return', 'Quarterly Returns', line_shape='hv', log_scale=True)

In [54]:
fig, ax = plt.subplots(figsize=(16,8))
data = final_df.loc['NVDA'].reset_index()
data_x= np.log(.2 + data.reportedEPS)
data_y = np.log(data.adjusted_close)
sns.scatterplot(x=data_x, y=data_y, ax=ax, s=1, alpha=1/3)
#ax.plot(x=final_df.loc['AAPL'].index, y=final_df.loc['AAPL'])

<Axes: xlabel='reportedEPS', ylabel='adjusted_close'>

In [23]:
#sns.pairplot(final_df.reset_index('tick'), hue='tick')

### Regression

In [55]:
final_df.columns

Index(['close', 'adjusted_close', 'reportedEPS', 'estimatedEPS',
       'reportedEPS_1', 'reportedEPS_2', 'reportedEPS_3', 'reportedEPS_4',
       'reportedEPS_5', 'reportedEPS_6', 'reportedEPS_7', 'daily_return',
       'weekly_return', 'quarterly_return'],
      dtype='object')

In [62]:
import statsmodels.formula.api as smf

k = 0.2
#cols = [f'np.log(k+reportedEPS_{i})' for i in range(1, 8)]
reg = smf.ols(f"np.log(adjusted_close) ~ np.log(k+estimatedEPS) + np.log(k+reportedEPS_1) + np.log(k+reportedEPS_2)", final_df).fit()
reg.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                              OLS Regression Results                              
==================================================================================
Dep. Variable:     np.log(adjusted_close)   R-squared:                       0.798
Model:                                OLS   Adj. R-squared:                  0.798
Method:                     Least Squares   F-statistic:                 2.138e+04
Date:                    Mon, 10 Jul 2023   Prob (F-statistic):               0.00
Time:                            01:18:05   Log-Likelihood:                -17273.
No. Observations:                   16200   AIC:                         3.455e+04
Df Residuals:                       16196   BIC:                         3.458e+04
Df Model:                               3                                         
Covariance Type:                nonrobust                                         
=============================================================================================
                                coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------------------
Intercept                     3.4479      0.006    563.044      0.000       3.436       3.460
np.log(k + estimatedEPS)     -0.5431      0.070     -7.810      0.000      -0.679      -0.407
np.log(k + reportedEPS_1)     1.3496      0.170      7.926      0.000       1.016       1.683
np.log(k + reportedEPS_2)     0.5506      0.158      3.495      0.000       0.242       0.859
==============================================================================
Omnibus:                     1013.704   Durbin-Watson:                   0.007
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             1225.537
Skew:                           0.633   Prob(JB):                    7.55e-267
Kurtosis:                       3.459   Cond. No.                         76.5
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

<class 'statsmodels.iolib.summary.Summary'>
"""
                              OLS Regression Results                              
==================================================================================
Dep. Variable:     np.log(adjusted_close)   R-squared:                       0.799
Model:                                OLS   Adj. R-squared:                  0.799
Method:                     Least Squares   F-statistic:                     8042.
Date:                    Mon, 10 Jul 2023   Prob (F-statistic):               0.00
Time:                            01:16:15   Log-Likelihood:                -17229.
No. Observations:                   16190   AIC:                         3.448e+04
Df Residuals:                       16181   BIC:                         3.454e+04
Df Model:                               8                                         
Covariance Type:                nonrobust                                         
=============================================================================================
                                coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------------------
Intercept                     3.4484      0.006    564.076      0.000       3.436       3.460
np.log(k + estimatedEPS)     -0.5781      0.070     -8.309      0.000      -0.714      -0.442
np.log(k + reportedEPS_1)     1.3822      0.170      8.130      0.000       1.049       1.716
np.log(k + reportedEPS_2)    -0.0041      0.222     -0.018      0.985      -0.440       0.431
np.log(k + reportedEPS_3)    -0.0166      0.221     -0.075      0.940      -0.451       0.418
np.log(k + reportedEPS_4)     0.0113      0.220      0.052      0.959      -0.420       0.442
np.log(k + reportedEPS_5)     0.0087      0.220      0.040      0.968      -0.422       0.439
np.log(k + reportedEPS_6)     0.0149      0.219      0.068      0.946      -0.415       0.445
np.log(k + reportedEPS_7)     0.5397      0.156      3.466      0.001       0.234       0.845
==============================================================================
Omnibus:                     1041.271   Durbin-Watson:                   0.008
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             1266.258
Skew:                           0.642   Prob(JB):                    1.09e-275
Kurtosis:                       3.476   Cond. No.                         165.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""